In [60]:
import vectorbtpro as vbt
import numpy as np
import pandas as pd
from numba import njit

# Enable Plotly Resampler globally
vbt.settings.plotting.use_resampler = True

@njit
def rolling_mean_nb(arr, window):
    out = np.empty_like(arr)
    for i in range(len(arr)):
        if i < window - 1:
            out[i] = np.nan
        else:
            out[i] = np.mean(arr[i - window + 1:i + 1])
    return out

@njit
def annualized_volatility_nb(returns, window):
    out = np.empty_like(returns)
    for i in range(len(returns)):
        if i < window - 1:
            out[i] = np.nan
        else:
            out[i] = np.std(returns[i - window + 1:i + 1]) * np.sqrt(365)
    return out

@njit
def determine_regime_nb(price, ma_short, ma_long, vol_short, avg_vol_threshold):
    regimes = np.empty_like(price, dtype=np.int32)
    for i in range(len(price)):
        if np.isnan(ma_short[i]) or np.isnan(ma_long[i]) or np.isnan(vol_short[i]):
            regimes[i] = -1  # Unknown
        elif price[i] > ma_short[i] and price[i] > ma_long[i]:
            if vol_short[i] > avg_vol_threshold:
                regimes[i] = 1  # Above Avg Vol Bull Trend
            else:
                regimes[i] = 2  # Below Avg Vol Bull Trend
        elif price[i] < ma_short[i] and price[i] < ma_long[i]:
            if vol_short[i] > avg_vol_threshold:
                regimes[i] = 3  # Above Avg Vol Bear Trend
            else:
                regimes[i] = 4  # Below Avg Vol Bear Trend
        else:
            if vol_short[i] > avg_vol_threshold:
                regimes[i] = 5  # Above Avg Vol Sideways
            else:
                regimes[i] = 6  # Below Avg Vol Sideways
    return regimes

@njit
def calculate_regimes_nb(price, returns, ma_short_window, ma_long_window, vol_short_window, avg_vol_window):
    ma_short = rolling_mean_nb(price, ma_short_window)
    ma_long = rolling_mean_nb(price, ma_long_window)
    vol_short = annualized_volatility_nb(returns, vol_short_window)
    avg_vol_threshold = np.nanmean(annualized_volatility_nb(returns, avg_vol_window))
    regimes = determine_regime_nb(price, ma_short, ma_long, vol_short, avg_vol_threshold)
    return regimes

RegimeIndicator = vbt.IndicatorFactory(
    class_name='RegimeIndicator',
    input_names=['price', 'returns'],
    param_names=['ma_short_window', 'ma_long_window', 'vol_short_window', 'avg_vol_window'],
    output_names=['regimes']
).with_apply_func(calculate_regimes_nb)

# # Example data
# btc_data = vbt.YFData.fetch('BTC-USD', end='2024-01-01')
# btc_data = btc_data.get()
# btc_data['Return'] = btc_data['Close'].pct_change()

# # Run the indicator
# regime_indicator = RegimeIndicator.run(
#     btc_data['Close'].values,
#     btc_data['Return'].values,
#     ma_short_window=21,
#     ma_long_window=88,
#     vol_short_window=21,
#     avg_vol_window=365
# )

# # Add regimes to DataFrame using .values
# btc_data['Market Regime'] = regime_indicator.regimes.values
# btc_data['Close'].vbt.overlay_with_heatmap(btc_data['Market Regime']).show()




# Run the individual strategies
        """
        Bollinger Bands LONG only BTC	1H 	If price closes below the lowest BB, buy, set stop and take profit 2.5 * ATR from entry
        Bollinger Bands LONG only ETH	1H 	If price closes below the lowest BB, buy, set stop and take profit 2.5 * ATR from entry
        Bollinger Bands SHORT only BTC	1H 	If price closes above the highest BB, sell, set stop and take profit 2.5 * ATR from entry
        Bollinger Bands SHORT only ETH	1H 	If price closes above the highest BB, sell, set stop and take profit 2.5 * ATR from entry
        """


In [38]:
# Strategy Regimes
# These names should match the config names of the strategies in config/strategy_configs
simple_ma_long_only_btc = [1, 2]
simple_ma_long_only_eth = [1, 2]
simple_ma_short_only_btc = [5, 6]
simple_ma_short_only_eth = [5, 6]
simple_macd_long_only_btc = [1, 2, 3]
simple_macd_long_only_eth = [1, 2]
simple_macd_short_only_btc = [4, 5, 6]
simple_macd_short_only_eth = [5, 6]
simple_rsi_divergence_long_only_btc = [1, 2, 3]
simple_bbands_limits_long_only_btc = [2]
simple_bbands_limits_long_only_eth = [2]
simple_bbands_limits_short_only_btc = [5, 6]
simple_bbands_limits_short_only_eth = [5, 6]

In [78]:
# Get the data
data = vbt.BinanceData.from_hdf("../data/m1_data.h5")


In [83]:
btc_1h = data.resample('1H').data['BTCUSDT']
btc_daily = data.resample('1D').data['BTCUSDT']
btc_daily['Return'] = btc_daily['Close'].pct_change()
eth_daily = data.resample('1D').data['ETHUSDT']
eth_daily['Return'] = eth_daily['Close'].pct_change()
eth_1h = data.resample('1H').data['ETHUSDT']

# Add regimes to DataFrame
btc_regime_indicator = RegimeIndicator.run(
    btc_daily['Close'], btc_daily['Return'], ma_short_window=21, ma_long_window=88, vol_short_window=21, avg_vol_window=365)
eth_regime_indicator = RegimeIndicator.run(
    eth_daily['Close'], eth_daily['Return'], ma_short_window=21, ma_long_window=88, vol_short_window=21, avg_vol_window=365)

btc_daily['Market Regime'] = btc_regime_indicator.regimes.values
eth_daily['Market Regime'] = eth_regime_indicator.regimes.values

In [85]:
# Define allowed regimes at the top
allowed_regimes = [2]
# Add regimes to DataFrame

# Resample the regime data to hourly frequency
btc_daily_regime_data = btc_daily['Market Regime']
btc_hourly_regime_data = btc_daily_regime_data.resample('1h').ffill()
eth_daily_regime_data = eth_daily['Market Regime']
eth_hourly_regime_data = eth_daily_regime_data.resample('1h').ffill()

# Align the hourly regime data with the btc DataFrame
btc_aligned_regime_data = btc_hourly_regime_data.reindex(btc_1h.index, method='ffill')
eth_aligned_regime_data = eth_hourly_regime_data.reindex(eth_1h.index, method='ffill')

def run_bbands_strategy(
    symbol_ohlcv_df: pd.DataFrame,
    regime_data: pd.Series,
    allowed_regimes: list,
    fees: float = 0.001
):
    # Calculate Bollinger Bands and ATR
    bbands_run = vbt.BBANDS.run(close=symbol_ohlcv_df['Close'], window=14, alpha=2)
    atr = vbt.ATR.run(
        high=symbol_ohlcv_df['High'],
        low=symbol_ohlcv_df['Low'],
        close=symbol_ohlcv_df['Close'],
        window=14,
    )

    # Determine long entries
    long_entries = (symbol_ohlcv_df['Close'] < bbands_run.lower) & (regime_data.isin(allowed_regimes))

    # Calculate stop loss and take profit levels
    atr_multiplier = 2.5
    sl_stop = symbol_ohlcv_df['Close'] - atr_multiplier * atr.atr
    tp_stop = symbol_ohlcv_df['Close'] + atr_multiplier * atr.atr

    # Create and return the portfolio
    pf = vbt.PF.from_signals(
        close=symbol_ohlcv_df['Close'],
        entries=long_entries,
        exits=None,  # We'll let the stop loss and take profit handle the exits
        fees=fees,
        sl_stop=sl_stop,
        tp_stop=tp_stop,
        delta_format="target",
    )

    return pf

# Test the function
btc_pf = run_bbands_strategy(btc_1h, btc_aligned_regime_data, allowed_regimes)
eth_pf = run_bbands_strategy(eth_1h, eth_aligned_regime_data, allowed_regimes)

# You can now analyze the portfolio
print(f'btc_pf.total_return: {btc_pf.total_return}')
print(f'eth_pf.total_return: {eth_pf.total_return}')
# Create a new series with only allowed regimes highlighted
allowed_regimes_only = btc_daily['Market Regime'].copy()
allowed_regimes_only[~allowed_regimes_only.isin(allowed_regimes)] = np.nan

# Plot with only allowed regimes highlighted, using daily data
btc_daily['Close'].vbt.overlay_with_heatmap(
    allowed_regimes_only,
).show()

btc_pf.plot().show()
eth_pf.plot().show()
display(pd.concat([btc_pf.stats(), eth_pf.stats()], axis=1, keys=['btc_bbands_long_only', 'eth_bbands_long_only']))

btc_pf.total_return: 1.0348977499104652
eth_pf.total_return: 1.6527941141403708


/Users/ericervin/miniforge3/envs/datascience/lib/python3.11/site-packages/jupyter_client/session.py:721: UserWarning:

Message serialization failed with:
Out of range float values are not JSON compliant
Supporting this message is deprecated in jupyter-client 7, please make sure your message is JSON-compliant



btc_bbands_long_only  \
Start Index                 2019-09-08 17:00:00+00:00   
End Index                   2024-07-12 20:00:00+00:00   
Total Duration                     1769 days 04:00:00   
Start Value                                     100.0   
Min Value                                   97.712257   
Max Value                                  207.907395   
End Value                                  203.489775   
Total Return [%]                           103.489775   
Benchmark Return [%]                          475.364   
Position Coverage [%]                       13.893076   
Max Gross Exposure [%]                          100.0   
Max Drawdown [%]                            15.905793   
Max Drawdown Duration               765 days 14:00:00   
Total Orders                                      362   
Total Fees Paid                             53.724007   
Total Trades                                      181   
Win Rate [%]                                64.640884   
Best Trade [%]                               5.013552   
Worst Trade [%]                             -4.992188   
Avg Winning Trade [%]                        1.863695   
Avg Losing Trade [%]                         -2.22996   
Avg Winning Trade Duration  1 days 09:01:32.307692307   
Avg Losing Trade Duration      1 days 07:47:48.750000   
Profit Factor                                1.484901   
Expectancy                                   0.571767   
Sharpe Ratio                                 1.066403   
Calmar Ratio                                 0.992468   
Omega Ratio                                  1.092298   
Sortino Ratio                                1.535663   

                                 eth_bbands_long_only  
Start Index                 2019-09-08 17:00:00+00:00  
End Index                   2024-07-12 20:00:00+00:00  
Total Duration                     1769 days 04:00:00  
Start Value                                     100.0  
Min Value                                   93.693884  
Max Value                                  310.173298  
End Value                                  265.279411  
Total Return [%]                           165.279411  
Benchmark Return [%]                      2026.363014  
Position Coverage [%]                       14.180405  
Max Gross Exposure [%]                          100.0  
Max Drawdown [%]                            14.473808  
Max Drawdown Duration               278 days 16:00:00  
Total Orders                                      356  
Total Fees Paid                              69.49471  
Total Trades                                      178  
Win Rate [%]                                62.921348  
Best Trade [%]                                6.58122  
Worst Trade [%]                             -5.502634  
Avg Winning Trade [%]                        2.599405  
Avg Losing Trade [%]                        -2.822726  
Avg Winning Trade Duration  1 days 06:08:02.142857142  
Avg Losing Trade Duration   1 days 16:05:27.272727272  
Profit Factor                                1.442785  
Expectancy                                   0.928536  
Sharpe Ratio                                 1.084309  
Calmar Ratio                                 1.540492  
Omega Ratio                                  1.093185  
Sortino Ratio                                1.551816

In [108]:
# Define allowed regimes at the top
allowed_regimes = [2]

# Resample the regime data to hourly frequency
btc_daily_regime_data = btc_daily['Market Regime']
btc_hourly_regime_data = btc_daily_regime_data.resample('1h').ffill()
eth_daily_regime_data = eth_daily['Market Regime']
eth_hourly_regime_data = eth_daily_regime_data.resample('1h').ffill()

# Align the hourly regime data with the btc and eth DataFrames
btc_aligned_regime_data = btc_hourly_regime_data.reindex(btc_1h.index, method='ffill')
eth_aligned_regime_data = eth_hourly_regime_data.reindex(eth_1h.index, method='ffill')

def run_bbands_strategy(
    symbol_ohlcv_df: pd.DataFrame,
    regime_data: pd.Series,
    allowed_regimes: list,
    fees: float = 0.001
):
    # Calculate Bollinger Bands and ATR
    bbands_run = vbt.BBANDS.run(close=symbol_ohlcv_df['Close'], window=14, alpha=2)
    atr = vbt.ATR.run(
        high=symbol_ohlcv_df['High'],
        low=symbol_ohlcv_df['Low'],
        close=symbol_ohlcv_df['Close'],
        window=14,
    )

    # Determine long entries
    long_entries = (symbol_ohlcv_df['Close'] < bbands_run.lower) & (regime_data.isin(allowed_regimes))

    # Create exit signals when leaving allowed regimes
    regime_exits = ~regime_data.isin(allowed_regimes)

    # Calculate stop loss and take profit levels
    atr_multiplier = 10
    sl_stop = symbol_ohlcv_df['Close'] - atr_multiplier * atr.atr
    tp_stop = symbol_ohlcv_df['Close'] + atr_multiplier * atr.atr

    # Create and return the portfolio
    pf = vbt.PF.from_signals(
        close=symbol_ohlcv_df['Close'],
        entries=long_entries,
        exits=regime_exits,  # Exit when leaving allowed regimes
        fees=fees,
        sl_stop=sl_stop,
        tp_stop=tp_stop,
        delta_format="target",
    )

    return pf

# Test the function
btc_pf = run_bbands_strategy(btc_1h, btc_aligned_regime_data, allowed_regimes)
eth_pf = run_bbands_strategy(eth_1h, eth_aligned_regime_data, allowed_regimes)

# Create a new series with only allowed regimes highlighted for BTC
btc_allowed_regimes_only = btc_daily['Market Regime'].copy()
btc_allowed_regimes_only[~btc_allowed_regimes_only.isin(allowed_regimes)] = np.nan

# Create a new series with only allowed regimes highlighted for ETH
eth_allowed_regimes_only = eth_daily['Market Regime'].copy()
eth_allowed_regimes_only[~eth_allowed_regimes_only.isin(allowed_regimes)] = np.nan

# Plot with only allowed regimes highlighted, using daily data for BTC
btc_daily['Close'].vbt.overlay_with_heatmap(
    btc_allowed_regimes_only,
    title='BTC BBands Strategy Regimes 2',
    height=200
).show()

# Plot with only allowed regimes highlighted, using daily data for ETH
eth_daily['Close'].vbt.overlay_with_heatmap(
    eth_allowed_regimes_only,
    title='ETH BBands Strategy Regimes 2',
    height=200
).show()
height = 600
btc_pf.plot(height=height, title='BTC BBands Strategy Regimes 2').show()
eth_pf.plot(height=height, title='ETH BBands Strategy Regimes 2').show()

display(pd.concat([btc_pf.stats(), eth_pf.stats()], axis=1, keys=['btc_bbands_long_only', 'eth_bbands_long_only']))

/Users/ericervin/miniforge3/envs/datascience/lib/python3.11/site-packages/jupyter_client/session.py:721: UserWarning:

Message serialization failed with:
Out of range float values are not JSON compliant
Supporting this message is deprecated in jupyter-client 7, please make sure your message is JSON-compliant



/Users/ericervin/miniforge3/envs/datascience/lib/python3.11/site-packages/jupyter_client/session.py:721: UserWarning:

Message serialization failed with:
Out of range float values are not JSON compliant
Supporting this message is deprecated in jupyter-client 7, please make sure your message is JSON-compliant



btc_bbands_long_only  \
Start Index                 2019-09-08 17:00:00+00:00   
End Index                   2024-07-12 20:00:00+00:00   
Total Duration                     1769 days 04:00:00   
Start Value                                     100.0   
Min Value                                     99.9001   
Max Value                                  749.290211   
End Value                                  724.593871   
Total Return [%]                           624.593871   
Benchmark Return [%]                          475.364   
Position Coverage [%]                       20.996232   
Max Gross Exposure [%]                          100.0   
Max Drawdown [%]                             14.87268   
Max Drawdown Duration               435 days 23:00:00   
Total Orders                                      146   
Total Fees Paid                             43.681062   
Total Trades                                       73   
Win Rate [%]                                75.342466   
Best Trade [%]                              12.076354   
Worst Trade [%]                             -6.579095   
Avg Winning Trade [%]                        4.673523   
Avg Losing Trade [%]                        -2.707662   
Avg Winning Trade Duration  5 days 04:53:27.272727272   
Avg Losing Trade Duration             4 days 17:40:00   
Profit Factor                                5.418666   
Expectancy                                    8.55608   
Sharpe Ratio                                 2.039612   
Calmar Ratio                                 3.393419   
Omega Ratio                                  1.156542   
Sortino Ratio                                3.032925   

                                 eth_bbands_long_only  
Start Index                 2019-09-08 17:00:00+00:00  
End Index                   2024-07-12 20:00:00+00:00  
Total Duration                     1769 days 04:00:00  
Start Value                                     100.0  
Min Value                                   98.048819  
Max Value                                 1371.480803  
End Value                                 1293.831568  
Total Return [%]                          1193.831568  
Benchmark Return [%]                      2026.363014  
Position Coverage [%]                       20.134244  
Max Gross Exposure [%]                          100.0  
Max Drawdown [%]                             15.28233  
Max Drawdown Duration               285 days 02:00:00  
Total Orders                                      136  
Total Fees Paid                             68.228229  
Total Trades                                       68  
Win Rate [%]                                66.176471  
Best Trade [%]                              16.873445  
Worst Trade [%]                             -6.083468  
Avg Winning Trade [%]                        7.302138  
Avg Losing Trade [%]                        -2.387772  
Avg Winning Trade Duration            5 days 05:09:20  
Avg Losing Trade Duration   5 days 06:49:33.913043478  
Profit Factor                                4.866466  
Expectancy                                  17.556347  
Sharpe Ratio                                 2.067873  
Calmar Ratio                                 4.553453  
Omega Ratio                                  1.159024  
Sortino Ratio                                3.062929

## Okay now let's do the moving average strategies


In [103]:
# Define allowed regimes at the top
allowed_regimes = [1, 2]

# Resample the regime data to hourly frequency
btc_daily_regime_data = btc_daily['Market Regime']
btc_hourly_regime_data = btc_daily_regime_data.resample('1h').ffill()
eth_daily_regime_data = eth_daily['Market Regime']
eth_hourly_regime_data = eth_daily_regime_data.resample('1h').ffill()

# Align the hourly regime data with the btc and eth DataFrames
btc_aligned_regime_data = btc_hourly_regime_data.reindex(btc_1h.index, method='ffill')
eth_aligned_regime_data = eth_hourly_regime_data.reindex(eth_1h.index, method='ffill')

def run_ma_strategy(
    symbol_ohlcv_df: pd.DataFrame,
    regime_data: pd.Series,
    allowed_regimes: list,
    fast_ma: int,
    slow_ma: int,
):
    
    fast_ma = vbt.MA.run(symbol_ohlcv_df.Close, window=fast_ma).ma
    slow_ma = vbt.MA.run(symbol_ohlcv_df.Close, window=slow_ma).ma
    
    long_entries = fast_ma > slow_ma
    long_exits = fast_ma < slow_ma
    
    # Add regime filter
    long_entries = long_entries & regime_data.isin(allowed_regimes)
    
    # Create exit signals when leaving allowed regimes
    regime_exits = ~regime_data.isin(allowed_regimes)
    
    # Combine regime exits with other exit conditions
    long_exits = long_exits | regime_exits
    
    # Run the simulation
    pf = vbt.PF.from_signals(
        close=symbol_ohlcv_df.Close,
        entries=long_entries,
        exits=long_exits,
    )
    
    return pf

btc_pf = run_ma_strategy(btc_1h, btc_aligned_regime_data, allowed_regimes, fast_ma=21, slow_ma=55)
eth_pf = run_ma_strategy(eth_1h, eth_aligned_regime_data, allowed_regimes, fast_ma=21, slow_ma=55)

# Create a new series with only allowed regimes highlighted for BTC
btc_allowed_regimes_only = btc_daily['Market Regime'].copy()
btc_allowed_regimes_only[~btc_allowed_regimes_only.isin(allowed_regimes)] = np.nan

# Create a new series with only allowed regimes highlighted for ETH
eth_allowed_regimes_only = eth_daily['Market Regime'].copy()
eth_allowed_regimes_only[~eth_allowed_regimes_only.isin(allowed_regimes)] = np.nan

# Plot with only allowed regimes highlighted, using daily data for BTC
btc_daily['Close'].vbt.overlay_with_heatmap(
    btc_allowed_regimes_only,
    title='BTC MA Strategy Regimes 1 & 2'
).show()

# Plot with only allowed regimes highlighted, using daily data for ETH
eth_daily['Close'].vbt.overlay_with_heatmap(
    eth_allowed_regimes_only,
    title='ETH MA Strategy Regimes 1 & 2'
).show()
height = 600
btc_pf.plot(height=height, title='BTC MA Strategy').show()
eth_pf.plot(height=height, title='ETH MA Strategy').show()

display(pd.concat([btc_pf.stats(), eth_pf.stats()], axis=1, keys=['btc_ma_long_only', 'eth_ma_long_only']))

/Users/ericervin/miniforge3/envs/datascience/lib/python3.11/site-packages/jupyter_client/session.py:721: UserWarning:

Message serialization failed with:
Out of range float values are not JSON compliant
Supporting this message is deprecated in jupyter-client 7, please make sure your message is JSON-compliant



/Users/ericervin/miniforge3/envs/datascience/lib/python3.11/site-packages/jupyter_client/session.py:721: UserWarning:

Message serialization failed with:
Out of range float values are not JSON compliant
Supporting this message is deprecated in jupyter-client 7, please make sure your message is JSON-compliant



btc_ma_long_only  \
Start Index                 2019-09-08 17:00:00+00:00   
End Index                   2024-07-12 20:00:00+00:00   
Total Duration                     1769 days 04:00:00   
Start Value                                     100.0   
Min Value                                   97.657659   
Max Value                                 6061.330865   
End Value                                 5812.309829   
Total Return [%]                          5712.309829   
Benchmark Return [%]                          475.364   
Position Coverage [%]                       27.590674   
Max Gross Exposure [%]                          100.0   
Max Drawdown [%]                            14.384204   
Max Drawdown Duration               211 days 20:00:00   
Total Orders                                      438   
Total Fees Paid                                   0.0   
Total Trades                                      219   
Win Rate [%]                                54.794521   
Best Trade [%]                              26.038334   
Worst Trade [%]                             -5.809357   
Avg Winning Trade [%]                        4.857824   
Avg Losing Trade [%]                        -1.470197   
Avg Winning Trade Duration            3 days 01:09:30   
Avg Losing Trade Duration   1 days 05:39:23.636363636   
Profit Factor                                3.579483   
Expectancy                                  26.083607   
Sharpe Ratio                                  2.86758   
Calmar Ratio                                 9.121789   
Omega Ratio                                  1.199215   
Sortino Ratio                                4.311949   

                                     eth_ma_long_only  
Start Index                 2019-09-08 17:00:00+00:00  
End Index                   2024-07-12 20:00:00+00:00  
Total Duration                     1769 days 04:00:00  
Start Value                                     100.0  
Min Value                                   96.897937  
Max Value                                10163.002226  
End Value                                 9720.931948  
Total Return [%]                          9620.931948  
Benchmark Return [%]                      2026.363014  
Position Coverage [%]                       25.697127  
Max Gross Exposure [%]                          100.0  
Max Drawdown [%]                            26.699264  
Max Drawdown Duration               121 days 08:00:00  
Total Orders                                      436  
Total Fees Paid                                   0.0  
Total Trades                                      218  
Win Rate [%]                                53.211009  
Best Trade [%]                              51.293208  
Worst Trade [%]                            -19.446032  
Avg Winning Trade [%]                        6.276085  
Avg Losing Trade [%]                        -2.108609  
Avg Winning Trade Duration  2 days 22:23:16.551724137  
Avg Losing Trade Duration   1 days 02:55:17.647058823  
Profit Factor                                 3.25673  
Expectancy                                  44.132715  
Sharpe Ratio                                 2.541732  
Calmar Ratio                                 5.883737  
Omega Ratio                                   1.17981  
Sortino Ratio                                 3.78658